random forest for refined dataset
- imputed with mean value of each column
- eliminate outliers and leverges after normalized

some observations:
- the model contructed by not normalized dataset is as good as the normalized dataset.

In [1]:
%matplotlib inline
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
from sklearn.ensemble import RandomForestRegressor

from sklearn.preprocessing import normalize
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split

from sklearn.model_selection import RandomizedSearchCV, GridSearchCV, cross_val_score
from sklearn.metrics import mean_squared_error, r2_score

from sklearn import tree
import joblib

import scipy

In [3]:
plt.rcParams["figure.figsize"] = (15, 10)

## load data

In [4]:
pth_data = '../processed_data/train_refine_not_norm_min.csv'
df_refine = pd.read_csv(pth_data)

In [5]:
df_refine

height  weight  gender        bmi   age      rh  heart_rate  \
0      1.63    50.0     1.0  18.818924  23.0  39.890   70.500000   
1      1.74    65.0    -1.0  21.469150  23.0  51.680   76.298872   
2      1.77    68.0    -1.0  21.705129  24.0  55.748   66.000000   
3      1.63    50.0     1.0  18.818924  23.0  34.850   74.000000   
4      1.77    58.0    -1.0  18.513199  23.0  51.275   97.000000   
..      ...     ...     ...        ...   ...     ...         ...   
280    1.63    50.0     1.0  18.818924  23.0  55.330   65.000000   
281    1.69    75.0    -1.0  26.259585  24.0  31.690   70.000000   
282    1.69    75.0    -1.0  26.259585  24.0  25.660  105.000000   
283    1.71    64.0    -1.0  21.887076  27.0  42.280   59.000000   
284    1.71    64.0    -1.0  21.887076  27.0  56.110   70.000000   

     stress_level  skin_temp       eda   Clo  Act  env_temp  
0       10.000000  32.215000  0.146231  0.50  1.0    76.876  
1       23.987342  31.672874  0.877379  0.36  1.0    80.206  
2        6.000000  33.353000  0.033414  0.54  1.0    74.467  
3       20.000000  31.672874  0.068829  0.50  1.0    74.964  
4       76.500000  32.215000  0.006481  0.36  1.0    77.770  
..            ...        ...       ...   ...  ...       ...  
280      9.000000  31.672874  0.009863  0.50  0.8    76.703  
281      0.000000  32.007000  0.012317  0.36  1.0    74.791  
282     23.987342  30.484000  0.002907  0.36  1.8    75.139  
283     23.000000  33.996000  0.068711  0.74  1.0    75.484  
284     24.000000  34.073000  0.107164  0.74  1.0    69.449  

[285 rows x 13 columns]

In [6]:
df_refine.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 285 entries, 0 to 284
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   height        285 non-null    float64
 1   weight        285 non-null    float64
 2   gender        285 non-null    float64
 3   bmi           285 non-null    float64
 4   age           285 non-null    float64
 5   rh            285 non-null    float64
 6   heart_rate    285 non-null    float64
 7   stress_level  285 non-null    float64
 8   skin_temp     285 non-null    float64
 9   eda           285 non-null    float64
 10  Clo           285 non-null    float64
 11  Act           285 non-null    float64
 12  env_temp      285 non-null    float64
dtypes: float64(13)
memory usage: 29.1 KB


## data process

### X & y

In [7]:
X_data = df_refine[['height', 'weight', 'gender', 'bmi', 'age', 'rh', \
                      'heart_rate', 'stress_level', 'skin_temp', 'eda', \
                      'Clo', 'Act']]

In [8]:
X_cols_name = X_data.columns

In [9]:
y_data = df_refine['env_temp']

### make training data and testing data

In [14]:
X_train, X_test, y_train, y_test = train_test_split(X_data, y_data, test_size=0.2, random_state=1208)

much better than the basic linear regression

## tuning hyperparameter
cross validation

### random search
Use the random grid to search for best hyperparameters (approximately)
- 5-fold cross validation

In [16]:
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]

# Number of features to consider at every split
max_features = ['auto', 'sqrt']

# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)

# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10, 15, 20]

# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4, 8, 16]

# Complexity parameter used for Minimal Cost-Complexity Pruning.
# ccp_alpha = [0.00001, 0.0005, 0.0001, 0.0005]
    
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf}

In [17]:
random_grid

{'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000],
 'max_features': ['auto', 'sqrt'],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None],
 'min_samples_split': [2, 5, 10, 15, 20],
 'min_samples_leaf': [1, 2, 4, 8, 16]}

In [18]:
rfr = RandomForestRegressor()

In [19]:
rfr_random = RandomizedSearchCV(estimator=rfr, 
                               param_distributions=random_grid, 
                               n_iter=100, 
                               cv=5, 
                               verbose=2, 
                               random_state=1208, 
                               n_jobs=-1,
                               scoring='r2')

In [20]:
# Fit the random search model
# Use R^2 as score method
rfr_random.fit(X_train, y_train)

Fitting 5 folds for each of 100 candidates, totalling 500 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    5.9s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   27.5s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:  1.0min
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:  1.5min finished


RandomizedSearchCV(cv=5, estimator=RandomForestRegressor(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4, 8, 16],
                                        'min_samples_split': [2, 5, 10, 15, 20],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=1208, scoring='r2', verbose=2)

In [21]:
rfr_random.best_params_

{'n_estimators': 1000,
 'min_samples_split': 2,
 'min_samples_leaf': 1,
 'max_features': 'sqrt',
 'max_depth': 90}

In [22]:
rfr_random.best_score_

0.4578585668975455

### Grid Search
Random search allowed us to narrow down the range for each hyperparameter. Now that we know where to concentrate our search, we can explicitly specify every combination of settings to try.

In [23]:
param_grid = {
    'n_estimators': [800, 900, 1000, 1100, 1200],
    'min_samples_split': [1, 2, 3],
    'min_samples_leaf': [1, 2, 3],
    'max_features': [2, 3, 4, 5],
    'max_depth': [70, 80, 90, 100, 110, None]
}

In [24]:
rfr = RandomForestRegressor()

In [25]:
grid_search = GridSearchCV(estimator = rfr, 
                           param_grid = param_grid, 
                           cv = 5, 
                           n_jobs = -1, 
                           verbose = 2,
                           scoring='r2')

In [26]:
grid_search.fit(X_train, y_train)

Fitting 5 folds for each of 1080 candidates, totalling 5400 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    1.1s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   15.8s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:   38.5s
[Parallel(n_jobs=-1)]: Done 624 tasks      | elapsed:  1.2min
[Parallel(n_jobs=-1)]: Done 989 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 1434 tasks      | elapsed:  2.7min
[Parallel(n_jobs=-1)]: Done 1961 tasks      | elapsed:  3.8min
[Parallel(n_jobs=-1)]: Done 2568 tasks      | elapsed:  4.9min
[Parallel(n_jobs=-1)]: Done 3257 tasks      | elapsed:  6.3min
[Parallel(n_jobs=-1)]: Done 4026 tasks      | elapsed:  7.8min
[Parallel(n_jobs=-1)]: Done 4877 tasks      | elapsed:  9.4min
[Parallel(n_jobs=-1)]: Done 5400 out of 5400 | elapsed: 10.4min finished


GridSearchCV(cv=5, estimator=RandomForestRegressor(), n_jobs=-1,
             param_grid={'max_depth': [70, 80, 90, 100, 110, None],
                         'max_features': [2, 3, 4, 5],
                         'min_samples_leaf': [1, 2, 3],
                         'min_samples_split': [1, 2, 3],
                         'n_estimators': [800, 900, 1000, 1100, 1200]},
             scoring='r2', verbose=2)

In [27]:
grid_search.best_params_

{'max_depth': 100,
 'max_features': 4,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'n_estimators': 800}

In [28]:
grid_search.best_score_

0.46457689817767134

### validate the result

In [29]:
best_params = grid_search.best_params_

In [30]:
rfr = RandomForestRegressor(random_state=1208)

In [31]:
rfr.set_params(**best_params)

RandomForestRegressor(max_depth=100, max_features=4, n_estimators=800,
                      random_state=1208)

In [32]:
rfr_cv_mse = cross_val_score(rfr, X_train, y_train, scoring='neg_mean_squared_error', cv=5)

In [33]:
rfr_cv_mse

array([-2.22914982, -3.09540137, -1.85541056, -2.28396946, -1.44072251])

In [34]:
np.abs(rfr_cv_mse.mean())

2.1809307450340634

In [35]:
rfr_cv_r2 = cross_val_score(rfr, X_train, y_train, scoring='r2', cv=5)

In [36]:
rfr_cv_r2

array([0.39026026, 0.24352163, 0.63176088, 0.503291  , 0.52237073])

In [37]:
np.abs(rfr_cv_r2.mean())

0.4582409000538277

## final model

In [49]:
best_params = grid_search.best_params_

In [50]:
rfr_best = RandomForestRegressor(random_state=1208)
rfr_best.set_params(**best_params)

RandomForestRegressor(max_depth=100, max_features=4, n_estimators=800,
                      random_state=1208)

In [51]:
rfr_best.fit(X_train, y_train)

RandomForestRegressor(max_depth=100, max_features=4, n_estimators=800,
                      random_state=1208)

### save model

In [52]:
filename = './min_random_forest_model.sav'
joblib.dump(rfr_best, filename)

['./min_random_forest_model.sav']

## visualization
pick a tree from the forest to visualize

In [53]:
plt.rcParams["figure.figsize"] = (600, 100)
a_tree = tree.plot_tree(rfr_best.estimators_[0], 
                        feature_names=X_data.columns, 
                        rounded=True,
                        filled=True,
                        fontsize=12)

## test

In [54]:
y_pred_test = rfr_best.predict(X_test)

In [55]:
y_pred_test

array([77.8729575 , 77.66955125, 75.91897375, 75.66193   , 77.41612   ,
       75.60589875, 77.1462925 , 74.714305  , 76.06178875, 76.927855  ,
       76.4461025 , 76.61222   , 75.25098375, 75.84258625, 76.68548125,
       76.453345  , 75.13615875, 75.170635  , 75.9777175 , 75.24051625,
       74.2163675 , 77.27317125, 75.016495  , 74.6061125 , 77.38071   ,
       75.21640125, 75.24631375, 76.794885  , 73.23543125, 77.28352688,
       75.91466625, 77.599275  , 76.30652   , 75.335175  , 76.9138425 ,
       74.9525475 , 76.65944875, 75.2969125 , 75.36264875, 76.363295  ,
       73.6366675 , 75.48528375, 75.80248875, 75.72660875, 72.63320125,
       76.2198475 , 75.35760875, 75.71972125, 76.40053375, 77.66959625,
       74.72975875, 76.87741125, 76.49084125, 74.76215   , 75.36342625,
       75.344085  , 76.59576125])

In [56]:
pd.DataFrame({'Actual': y_test, 'Predicted': y_pred_test})

Actual  Predicted
166  78.514  77.872957
25   79.502  77.669551
229  76.354  75.918974
217  74.964  75.661930
10   76.528  77.416120
71   74.619  75.605899
100  76.181  77.146293
152  73.407  74.714305
145  76.375  76.061789
238  77.509  76.927855
235  77.029  76.446102
53   77.574  76.612220
232  74.791  75.250984
157  76.181  75.842586
282  75.139  76.685481
28   76.550  76.453345
123  74.683  75.136159
23   74.619  75.170635
24   76.181  75.977718
48   75.312  75.240516
68   71.361  74.216368
165  77.050  77.273171
7    74.964  75.016495
19   74.271  74.606112
255  78.208  77.380710
54   75.312  75.216401
124  74.964  75.246314
101  77.553  76.794885
11   72.739  73.235431
200  77.574  77.283527
256  74.619  75.914666
203  78.076  77.599275
183  76.246  76.306520
155  74.271  75.335175
276  76.703  76.913843
49   74.856  74.952548
189  77.378  76.659449
212  75.484  75.296912
83   73.753  75.362649
136  75.508  76.363295
107  74.381  73.636667
161  74.791  75.485284
259  76.181  75.802489
180  77.292  75.726609
37   71.447  72.633201
27   75.659  76.219847
204  75.659  75.357609
234  77.029  75.719721
134  75.420  76.400534
52   78.975  77.669596
252  76.181  74.729759
267  77.574  76.877411
177  75.029  76.490841
216  74.597  74.762150
117  75.484  75.363426
246  73.926  75.344085
4    77.770  76.595761

In [57]:
# mean squared error
mean_squared_error(y_test, y_pred_test)

0.8558057058418344

In [58]:
# R2 score
r2_score(y_test, y_pred_test)

0.6877711859721547

## save test dataset

In [59]:
test_df = X_test.copy()

In [61]:
test_df['env_temp'] = 0

In [63]:
test_df['env_temp'] = y_test

In [66]:
test_df.to_csv('../processed_data/test_min.csv')

In [67]:
test_df

height  weight  gender        bmi   age      rh  heart_rate  \
166    1.77    68.0    -1.0  21.705129  24.0  57.779   76.298872   
25     1.83    74.0    -1.0  22.096808  24.0  46.650   84.000000   
229    1.63    50.0     1.0  18.818924  23.0  41.050   86.000000   
217    1.63    50.0     1.0  18.818924  23.0  39.170   67.000000   
10     1.63    50.0     1.0  18.818924  23.0  54.550   79.000000   
71     1.69    75.0    -1.0  26.259585  24.0  28.920  102.000000   
100    1.63    50.0     1.0  18.818924  23.0  51.410   76.298872   
152    1.67    56.0     1.0  20.079601  26.0  59.560   76.298872   
145    1.77    68.0    -1.0  21.705129  24.0  53.962   86.000000   
238    1.77    58.0    -1.0  18.513199  23.0  53.134   92.000000   
235    1.77    68.0    -1.0  21.705129  24.0  60.468   84.000000   
53     1.63    50.0     1.0  18.818924  23.0  52.990   70.000000   
232    1.78    73.0    -1.0  23.040020  24.0  65.000   87.000000   
157    1.63    50.0     1.0  18.818924  23.0  40.740   76.000000   
282    1.69    75.0    -1.0  26.259585  24.0  25.660  105.000000   
28     1.77    68.0    -1.0  21.705129  24.0  55.759   78.000000   
123    1.77    68.0    -1.0  21.705129  24.0  54.895   63.500000   
23     1.63    50.0     1.0  18.818924  23.0  31.880   61.500000   
24     1.69    75.0    -1.0  26.259585  24.0  28.900   86.000000   
48     1.69    75.0    -1.0  26.259585  24.0  33.440   76.298872   
68     1.60    52.5     1.0  20.507812  24.0  48.105   77.000000   
165    1.69    75.0    -1.0  26.259585  24.0  50.720  106.000000   
7      1.63    50.0     1.0  18.818924  23.0  28.430   67.000000   
19     1.63    50.0     1.0  18.818924  23.0  21.910   65.000000   
255    1.77    58.0    -1.0  18.513199  23.0  54.292   88.000000   
54     1.63    50.0     1.0  18.818924  23.0  34.870   72.000000   
124    1.69    75.0    -1.0  26.259585  24.0  33.130   76.298872   
101    1.77    58.0    -1.0  18.513199  23.0  52.915   80.000000   
11     1.60    52.5     1.0  20.507812  24.0  34.698   85.000000   
200    1.63    50.0     1.0  18.818924  23.0  53.260   84.000000   
256    1.69    75.0    -1.0  26.259585  24.0  26.190   92.000000   
203    1.64    54.0     1.0  20.077335  24.0  61.437   73.000000   
183    1.77    68.0    -1.0  21.705129  24.0  50.876   77.000000   
155    1.63    50.0     1.0  18.818924  23.0  30.710   78.000000   
276    1.63    50.0     1.0  18.818924  23.0  54.670   64.000000   
49     1.60    52.5     1.0  20.507812  24.0  42.886   61.000000   
189    1.77    68.0    -1.0  21.705129  24.0  56.012   76.298872   
212    1.63    50.0     1.0  18.818924  23.0  25.740   76.000000   
83     1.63    50.0     1.0  18.818924  23.0  30.790   65.500000   
136    1.77    68.0    -1.0  21.705129  24.0  50.374   76.000000   
107    1.60    52.5     1.0  20.507812  24.0  40.279   69.500000   
161    1.63    50.0     1.0  18.818924  23.0  26.550   60.000000   
259    1.71    64.0    -1.0  21.887076  27.0  57.270   76.298872   
180    1.60    52.5     1.0  20.507812  24.0  50.664   76.298872   
37     1.60    52.5     1.0  20.507812  24.0  44.556   72.000000   
27     1.63    50.0     1.0  18.818924  23.0  39.370   76.000000   
204    1.69    75.0    -1.0  26.259585  24.0  34.490   69.000000   
234    1.77    68.0    -1.0  21.705129  24.0  55.204   69.000000   
134    1.77    68.0    -1.0  21.705129  24.0  50.400   85.000000   
52     1.69    75.0    -1.0  26.259585  24.0  54.760   90.000000   
252    1.71    64.0    -1.0  21.887076  27.0  41.380   62.000000   
267    1.63    50.0     1.0  18.818924  23.0  54.400   71.500000   
177    1.77    68.0    -1.0  21.705129  24.0  55.296   94.000000   
216    1.77    68.0    -1.0  21.705129  24.0  56.068   61.000000   
117    1.66    57.0     1.0  20.685150  25.0  41.950   76.298872   
246    1.63    50.0     1.0  18.818924  23.0  30.370   79.000000   
4      1.77    58.0    -1.0  18.513199  23.0  51.275   97.000000   

     stress_level  skin_temp       eda   Clo  Act  env_temp 